In [1]:
import re
import numpy as np
import pandas as pd
import geopandas as gpd

# Assignment 6 Part 2
## Interactive web maps with Folium and Leaflet

### Pull GeoJSON using API

In [2]:
from pyrestcli.auth import NoAuthClient
from carto.sql import SQLClient

In [3]:
sql = SQLClient(NoAuthClient('https://phl.carto.com'))

col   = ',\n       '.join(['ownername','opa_account_num',
                           'address','zip',
                           'prioritydesc',
                           'violationtype','violationdescription',
                           'the_geom'])
table = 'li_violations'
cond  = '\n  and  '.join(["extract(year from violationdate) = 2018",
                          #"substring(zip from 1 for 5) in ('19104','19139','19143')",
                          "status is null",
                          "prioritydesc in ('UNSAFE','HAZARD','IMMINENTLY DANGEROUS')"])

query = '''
select %s 
from   %s 
where  %s
''' %(col,table,cond)

In [4]:
rsp = sql.send(query, format = 'geojson')

C:\Users\Jonathan\Documents\Anaconda3\envs\musa-620\lib\site-packages\pyrestcli\auth.py:79: UserWarning: You are using methods other than get with no authentication!!!
  warnings.warn(_("You are using methods other than get with no authentication!!!"))


In [5]:
viol = gpd.GeoDataFrame.from_features(rsp)
viol = viol.loc[viol.geometry.notnull()]
viol.crs = {'init' :'epsg:4326'}

### Plot points using Folium

In [6]:
import folium

In [14]:
map = folium.Map(
    location = [39.99, -75.13],
    zoom_start = 11,
    
#     min_zoom   = 10,
#     max_zoom   = 19,
    
#     max_bounds = True,
#     min_lat = viol.bounds['miny'].min(),
#     max_lat = viol.bounds['maxy'].max(),
#     min_lon = viol.bounds['minx'].min(),
#     max_lon = viol.bounds['maxx'].max(),

    tiles = 'CartoDB dark_matter',
    attr  = '&copy; <a href="https://www.openstreetmap.org/copyright">OpenStreetMap</a> contributors'
)

# map.fit_bounds([[viol.bounds['miny'].min(),viol.bounds['minx'].min()],
#                 [viol.bounds['maxy'].max(),viol.bounds['maxx'].max()]])

In [8]:
def style(feature):
    value = feature['prioritydesc']
    color = '#000000',
    color = '#ffeda0' if value == 'UNSAFE' else color
    color = '#feb24c' if value == 'HAZARD' else color
    color = '#f03b20' if value == 'IMMINENTLY DANGEROUS' else color
    return color

In [15]:
layer = folium.FeatureGroup(name = "Dangerous Building Code Violations (2018)")

for i,v in viol.iterrows():
    
    popup = '''
    <h4 style="text-align:center;background-color:%s;padding:3px;">%s</h4>
    <p>%s (OPA&num;&nbsp;%s)</p>
    <p>%s<br>PHILADELPHIA, PA %s</p>
    <p><strong>Violation Type: %s</strong><br>%s</p>
    ''' %(style(v),v['prioritydesc'],
          re.sub(' {2,}',', ',str(v['ownername'])),
          v['opa_account_num'],
          v['address'],v['zip'],
          v['violationtype'],v['violationdescription'])
    
    folium.CircleMarker(location = (v.geometry.y,v.geometry.x),
                        radius   = 3,
                        color    = style(v),
                        popup    = folium.Popup(popup,max_width = 200),
                        fill     = False
                       ).add_to(layer)

### Plot heatmap using Leaflet.heat

In [10]:
import folium.plugins

In [11]:
viol['lat'] = viol.geometry.y
viol['lng'] = viol.geometry.x

heat = folium.plugins.HeatMap(
    viol[['lat', 'lng']].values,
    name = 'Heat Map of Dangerous Violations (2018)',
    show = False
)

### Save map 

In [16]:
layer.add_to(map);
heat.add_to(map);
folium.LayerControl().add_to(map)

map.save('Part2.html')
map

Note: The heatmap is hidden by default. Use the Layer Control to show it.

### [Observable map](https://observablehq.com/@jonoyuan/assignment-6-part-2)